# Imports

In [1]:
from OSMPythonTools.nominatim import Nominatim
import plotly.express as px
import plotly.io as pio
from PIL import Image
import pandas as pd
import kaleido
import imageio
import folium
import os
import io

pio.renderers.default = "plotly_mimetype+notebook_connected"
pio.templates.default = "none"

# Data Transformation

In [13]:
# https://www.kaggle.com/datasets/paultimothymooney/latitude-and-longitude-for-every-country-and-state
geo = pd.read_csv('./data/world_country_and_usa_states_latitude_and_longitude_values.csv')
geo = geo[['usa_state_code', 'usa_state', 'usa_state_latitude', 'usa_state_longitude']].dropna()

te = pd.read_csv('./data/train_final.csv')
te = te[['DATE', 'TYPE', 'STATE', 'CASKLDRR', 'CASINJRR']]
te['DATE'] = pd.to_datetime(te['DATE'])
te['CASKLDRR'] = te['CASKLDRR'].astype(int)
te['CASINJRR'] = te['CASINJRR'].astype(int)

ap = pd.read_csv('./data/airplanes_final.csv')
ap = ap[['Date', 'Fatalities', 'Ground', 'State']]
ap['DATE'] = pd.to_datetime(ap['Date'])
ap['Fatalities'] = ap['Fatalities'].astype(int)
ap['Ground'] = ap['Ground'].fillna(0)
ap['Ground'] = ap['Ground'].astype(int)

In [14]:
geo.rename(columns={'usa_state_code':'STATE', 'usa_state':'STATE_NAME', 'usa_state_latitude':'LAT', 'usa_state_longitude':'LON'}, inplace=True)

te_agg = te.groupby([te['DATE'].dt.year, te['STATE']])[['CASKLDRR', 'CASINJRR']].sum().reset_index()
te_agg.rename(columns={'DATE': 'YEAR'}, inplace=True)
te_merged = pd.merge(te_agg, geo, how='inner', on='STATE')
te_options = ['CASKLDRR', 'CASINJRR']

ap_agg = ap.groupby([ap['DATE'].dt.year, ap['State']])[['Fatalities', 'Ground']].sum().reset_index()
ap_agg.rename(columns={'DATE': 'YEAR', 'State':'STATE', 'Fatalities':'KLDAP', 'Ground':'GKLDAP'}, inplace=True)
ap_merged = pd.merge(ap_agg, geo, how='inner', on='STATE')
ap_options = ['KLDAP', 'GKLDAP']

names = {
    'CASKLDRR':"Railroad Deaths",
    'CASINJRR':"Railroad Injuries",
    'KLDAP':"Plane Aircraft Deaths",
    'GKLDAP':"Plane Ground Deaths"
}

# Plot Choropleths

In [37]:
def create_choropleth(df, names, option, color):
    df = df.sort_values('YEAR')
    name = names[option]
    years = sorted(df['YEAR'].unique())
    min_value = df[option].min()
    max_value = df[option].max()

    fig = px.choropleth(
        df,
        locations="STATE",
        color=option,
        color_continuous_scale=color,
        hover_name="STATE_NAME",
        hover_data={option: True},
        animation_frame="YEAR",
        locationmode="USA-states",
        scope="usa",
        labels={option: name},
        title=f"{name} from {years[0]} to {years[-1]}",
        range_color=(min_value, max_value)
    )

    # add animation controls
    fig.layout.updatemenus[0].buttons[0].args[1]["frame"]["duration"] = 500
    fig.layout.updatemenus[0].buttons[0].args[1]["transition"]["duration"] = 0
    fig.layout.sliders[0].pad.t = 10

    fig.show()
    return fig

## Trains

In [38]:
rr_death = create_choropleth(te_merged, names, te_options[0], "Greens")

In [39]:
rr_inj = create_choropleth(te_merged, names, te_options[1], "Greens")

## Airplanes

In [41]:
ap_airdeaths = create_choropleth(ap_merged, names, ap_options[0], "Blues")

In [42]:
ap_gdeaths = create_choropleth(ap_merged, names, ap_options[1], "Blues")

# Save Imgs as HTML

In [43]:
base_path = "./img/choropleth/"
imgs = [rr_death, rr_inj, ap_airdeaths, ap_gdeaths]
img_names = ['CASKLDRR', 'CASINJRR', 'KLDAP', 'GKLDAP']

for i, img in enumerate(imgs):
    pio.write_html(img, file=f'{base_path}{img_names[i]}.html')

# Folium Plots

In [45]:
nominatim = Nominatim()
    
country_loc = nominatim.query("United States").toJSON()[0]
country_lat = country_loc['lat']
country_lon = country_loc['lon']

default_zoom = 4
max_width = 300

[nominatim] downloading data: search


In [47]:
def create_folium_map(base_map, df, options, color, type):
    # iterate through te_merged rows and add markers w/ popup    
    for index, row in df.iterrows():
        if row[options[0]] > 0 or row[options[1]] > 0: # only show incidents where people were injured/died
            popup_info = f"<b>Year:</b> {row['YEAR']}<br><b>State:</b> {row['STATE_NAME']}<br>"
            
            if type == "Railroad":
                popup_info += f"<b>Deaths:</b> {row[options[0]]}<br><b>Injuries:</b> {row[options[1]]}"
            elif type == "Airplane":
                popup_info += f"<b>Aircraft Deaths:</b> {row[options[0]]}<br><b>Ground Deaths:</b> {row[options[1]]}"
            
            popup = folium.Popup(popup_info, max_width=max_width)
            
            folium.Marker(
                location=[row['LAT'], row['LON']],
                icon=folium.Icon(color=color),
                popup=popup
            ).add_to(base_map)

## Trains

In [48]:
# create base map
train_map = folium.Map(location=[country_lat, country_lon], zoom_start=default_zoom)

create_folium_map(train_map, te_merged, te_options, "green", "Railroad")
train_map

## Airplanes

In [49]:
# create base map
plane_map = folium.Map(location=[country_lat, country_lon], zoom_start=default_zoom)

create_folium_map(plane_map, ap_merged, ap_options, "blue", "Airplane")
plane_map

In [50]:
for i, map in enumerate([train_map, plane_map]):
    name = "folium_train" if i==0 else "folium_plane"
    map.save(f'{base_path}{name}.html')